In [1]:
#pip install selenium
#pip install webdriver-manager

from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
from time import sleep
from random import randint
import requests
import re
from bs4 import BeautifulSoup
import urllib.request
import pandas as pd
import csv
from selenium.webdriver.support.ui import WebDriverWait

import findspark
findspark.init()

import pyspark
from pyspark.sql import SparkSession, SQLContext, functions
from pyspark.sql.functions import *
from pyspark.sql.types import *

import matplotlib.pyplot as plt

spark = SparkSession.builder.appName("MovieRecommender").getOrCreate()

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


22/11/26 13:24:52 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [2]:
movies=[]
years_url = [str(i) for i in range(2002,2023)]
pages = [str(i) for i in range(1, 10000, 50)]
for year_url in years_url:
    for page in pages:
        try:
            url = "https://www.imdb.com/search/title/?release_date=" + year_url + "&start=" + page
            page = urllib.request.urlopen(url)
            page_source = BeautifulSoup(page, "html.parser")
            driver = webdriver.Chrome(ChromeDriverManager().install())
            driver.get(url)
            driver.implicitly_wait(1)
            for item in page_source.find_all(class_='lister-item mode-advanced'):
                try:
                    movieid = item.find(class_='ribbonize')
                    movieid = movieid['data-tconst']
                except:
                    movieid = "NaN"
                try:
                    name = item.find('h3', {'class':'lister-item-header'})
                    name = name.find('a').get_text(strip=True)
                except:
                    name = "NaN"
                try:
                    year = item.find(class_='lister-item-year text-muted unbold').get_text(strip=True)
                except:
                    year = "NaN"
                try:
                    genre = item.find(class_='genre').get_text(strip=True)
                except:
                    genre = "NaN"
                try:
                    content = item.select('p')[1].get_text(strip=True)
                except:
                    content = "NaN"
                try:
                    rating = item.find(class_='inline-block ratings-imdb-rating').get_text(strip=True)
                except:
                    rating = "NaN"
                try:
                    score = item.find('span', {'class':'metascore'}).get_text(strip=True)
                except:
                    score = "NaN"
                try:
                    star = item.find('p', {'class':''}).get_text(strip=True)
                except:
                    star = "NaN"
                try:
                    votes = item.find('span', attrs = {'name':'nv'})
                    votes = votes['data-value'] 
                except:
                    vote = "NaN"
                movies.append({'MovieID' : movieid,
                                'MovieName' : name, 
                                'Year' : year,
                                'Genre': genre,
                                'Content': content,
                                'Star' : star,
                                'Rating' : rating, 
                                'Votes' : votes,
                              'Metascore' : score})
        except:
            pass
dataframe = pd.DataFrame(data=movies)
print(dataframe)
dataframe.to_csv('Movie/'f'PandasMovie.csv')
schema = StructType([ \
    StructField('MovieID',StringType(),True), \
    StructField('MovieName',StringType(),True), \
    StructField('Year',StringType(),True), \
    StructField('Genre',StringType(),True), \
    StructField('Content',StringType(),True), \
    StructField('Star',StringType(),True), \
    StructField('Rating',StringType(),True), \
    StructField('Votes',StringType(),True), \
    StructField('Metascore', StringType(), True)])
moviedata=spark.createDataFrame(data=movies,schema=schema)
moviedata.show()
moviedata.write.option("header",True).option("delimiter","|").csv('Movie/'f'SparkMovie.csv')

/tmp/ipykernel_19988/1794441476.py:10: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())
[WDM] - Downloading: 100%|█████████████████| 6.35M/6.35M [00:00<00:00, 10.9MB/s]


           MovieID                          MovieName         Year  \
0        tt0306414                 Đường Dây Tội Phạm  (2002–2008)   
1        tt0145487                         Người Nhện       (2002)   
2        tt0304669                    Ông Già Tuyết 2       (2002)   
3        tt0295297  Harry Potter và Phòng Chứa Bí Mật       (2002)   
4        tt0312172                               Monk  (2002–2009)   
...            ...                                ...          ...   
209990  tt13099434        NGFL: Nice Guys Finish Last       (2022)   
209991   tt8811670                   The Library Boys       (2022)   
209992  tt15226984         Once upon a time in Serbia       (2022)   
209993  tt20159188                   Elektra, My Love       (2022)   
209994  tt13323300                          Army Baby       (2022)   

                             Genre  \
0           Crime, Drama, Thriller   
1        Action, Adventure, Sci-Fi   
2          Comedy, Family, Fantasy   
3      

22/11/26 02:06:21 WARN PythonRunner: Detected deadlock while completing task 0.0 in stage 0 (TID 0): Attempting to kill Python Worker


+---------+--------------------+-----------+--------------------+--------------------+--------------------+------+-------+---------+
|  MovieID|           MovieName|       Year|               Genre|             Content|                Star|Rating|  Votes|Metascore|
+---------+--------------------+-----------+--------------------+--------------------+--------------------+------+-------+---------+
|tt0306414|  Đường Dây Tội Phạm|(2002–2008)|Crime, Drama, Thr...|The Baltimore dru...|Stars:Dominic Wes...|   9.3| 339003|      NaN|
|tt0145487|          Người Nhện|     (2002)|Action, Adventure...|After being bitte...|Director:Sam Raim...|   7.4| 815798|       73|
|tt0304669|     Ông Già Tuyết 2|     (2002)|Comedy, Family, F...|Scott Calvin has ...|Director:Michael ...|   5.7|  57807|       48|
|tt0295297|Harry Potter và P...|     (2002)|Adventure, Family...|An ancient prophe...|Director:Chris Co...|   7.4| 633363|       63|
|tt0312172|                Monk|(2002–2009)|Comedy, Crime, Drama|The 

In [5]:
movies=[]
years_url = [str(i) for i in range(2002,2005)]
pages = [str(i) for i in range(1, 100, 50)]
for year_url in years_url:
    for page in pages:
        try:
            url = "https://www.imdb.com/search/title/?release_date=" + year_url + "&start=" + page
            page = urllib.request.urlopen(url)
            page_source = BeautifulSoup(page, "html.parser")
            driver = webdriver.Chrome(ChromeDriverManager().install())
            driver.get(url)
            driver.implicitly_wait(1)
            for item in page_source.find_all(class_='lister-item mode-advanced'):
                try:
                    movieid = item.find(class_='ribbonize')
                    movieid = movieid['data-tconst']
                except:
                    movieid = "NaN"
                try:
                    name = item.find('h3', {'class':'lister-item-header'})
                    name = name.find('a').get_text(strip=True)
                except:
                    name = "NaN"
                try:
                    year = item.find(class_='lister-item-year text-muted unbold').get_text(strip=True)
                except:
                    year = "NaN"
                try:
                    genre = item.find(class_='genre').get_text(strip=True)
                except:
                    genre = "NaN"
                try:
                    content = item.select('p')[1].get_text(strip=True)
                except:
                    content = "NaN"
                try:
                    rating = item.find(class_='inline-block ratings-imdb-rating').get_text(strip=True)
                except:
                    rating = "NaN"
                try:
                    score = item.find('span', {'class':'metascore'}).get_text(strip=True)
                except:
                    score = "NaN"
                try:
                    star = item.find('p', {'class':''}).get_text(strip=True)
                except:
                    star = "NaN"
                try:
                    votes = item.find('span', attrs = {'name':'nv'})
                    votes = votes['data-value'] 
                except:
                    vote = "NaN"
                movies.append({'MovieID' : movieid,
                                'MovieName' : name, 
                                'Year' : year,
                                'Genre': genre,
                                'Content': content,
                                'Star' : star,
                                'Rating' : rating, 
                                'Votes' : votes,
                              'Metascore' : score})
        except:
            pass
dataframe = pd.DataFrame(data=movies)
print(dataframe)
dataframe.to_csv('Movie/'f'PandasMovieTest.csv')
schema = StructType([ \
    StructField('MovieID',StringType(),True), \
    StructField('MovieName',StringType(),True), \
    StructField('Year',StringType(),True), \
    StructField('Genre',StringType(),True), \
    StructField('Content',StringType(),True), \
    StructField('Star',StringType(),True), \
    StructField('Rating',StringType(),True), \
    StructField('Votes',StringType(),True), \
    StructField('Metascore', StringType(), True)])
moviedata=spark.createDataFrame(data=movies,schema=schema)
moviedata.show()
moviedata.write.option("header",True).option("delimiter","|").csv('Movie/'f'SparkMovieTest.csv')

/tmp/ipykernel_12824/3151998373.py:10: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


       MovieID                          MovieName         Year  \
0    tt0306414                 Đường Dây Tội Phạm  (2002–2008)   
1    tt0145487                         Người Nhện       (2002)   
2    tt0304669                    Ông Già Tuyết 2       (2002)   
3    tt0295297  Harry Potter và Phòng Chứa Bí Mật       (2002)   
4    tt0312172                               Monk  (2002–2009)   
..         ...                                ...          ...   
295  tt0395169                   Khách Sạn Rwanda       (2004)   
296  tt0390384                      Máy Thời Gian       (2004)   
297  tt0390022                Friday Night Lights       (2004)   
298  tt0331953                         Club Dread       (2004)   
299  tt0371246                          Spanglish       (2004)   

                          Genre  \
0        Crime, Drama, Thriller   
1     Action, Adventure, Sci-Fi   
2       Comedy, Family, Fantasy   
3    Adventure, Family, Fantasy   
4          Comedy, Crime, Drama 

AnalysisException: path file:/home/user/anaconda3/IMDB Movie Data/Movie/SparkMovieTest.csv already exists.

In [7]:
data = spark.read.option("header",True).option("sep","|").csv("SparkMovie.csv")
dataframe = data.toPandas()
print(dataframe)

           MovieID                             MovieName         Year  \
0        tt9114286  Chiến Binh Báo Đen: Wakanda Bất Diệt       (2022)   
1        tt4786824                           Hoàng Quyền     (2016– )   
2       tt13406094          Khu Nghỉ Dưỡng Hoa Sen Trắng  (2021–2022)   
3       tt14641788                        Enola Holmes 2       (2022)   
4        tt9253284                                 Andor     (2022– )   
...            ...                                   ...          ...   
182843  tt15671584                                 Paint       (2023)   
182844  tt20160210           The World's Worst Porn Film       (2022)   
182845  tt16996614              Bridge to the Other Side       (2022)   
182846  tt14962428                     L'année du requin       (2022)   
182847   tt2191811                          Silent Voice         None   

                            Genre  \
0        Action, Adventure, Drama   
1       Biography, Drama, History   
2           

In [2]:
def get_review():
    
    data = spark.read.option("header",True).option("sep","|").csv("moviedata.csv")
    moviedata = data.toPandas()
    #After the webpage opened, we can extract data of each movies
    #Set initial empty list for each element:
    for i in range(len(moviedata['MovieID'])): 
        driver = webdriver.Chrome(ChromeDriverManager().install())
        url = "https://www.imdb.com/title/" + moviedata['MovieID'][i] + "/reviews?"
        driver.get(url)
        # let webdriver wait for 3 seconds for the page to load
        driver.implicitly_wait(3)
        # Set up action to click on 'load more' button
        page = 1
        # 0-1000 review => 40 pages
        while page<=40:  
            try:
                #find the load more button on the webpage
                load_more = driver.find_element(By.ID, 'load-more-trigger')
                #click on that button
                load_more.click()
                #move on to next loadmore button
                page+=1
            except:
                #If couldnt find any button to click, stop
                break
        # After fully expand the page, grab data from whole website
        review = driver.find_elements(By.CLASS_NAME, 'lister-item')
        #Set list for each element:
        title = []
        review_id = []
        content = []
        rate = []
        date = []
        user_id = []
        user_name = []
        #run for loop to get 
        for n in range(0,1000):
            try: 
                #Grab each element before append them to the list
                reviewtitle = review[n].find_element(By.CLASS_NAME, 'title').text
                reviewcontent = review[n].find_element(By.CLASS_NAME, 'content').get_attribute("textContent")
                reviewrate = review[n].find_element(By.CLASS_NAME, 'rating-other-user-rating').text
                reviewdate = review[n].find_element(By.CLASS_NAME, 'review-date').text
                userid = review[n].find_element(By.CLASS_NAME, 'display-name-link').get_attribute("innerHTML")
                username = review[n].find_element(By.CLASS_NAME, 'display-name-link').text
                reviewid = review[n].get_attribute('data-review-id')

                #Then add them to the list
                review_id.append(reviewid)
                user_id.append(userid)
                title.append(reviewtitle)
                content.append(reviewcontent)
                rate.append(reviewrate)
                date.append(reviewdate)
                user_name.append(username)
            except:
                continue
                
        reviewdata = {'Review_ID' : review_id,
                    'User_ID' : user_id,
                    'User_name' : user_name,
                    'Review_title' : title, 
                    'Review_rate' : rate,
                    'Review_date' : date,
                    'Review_body' : content}
        #Create dataframe for each review movie to export
        review = pd.DataFrame(data = reviewdata)
        movie = moviedata['MovieID'][i] 
        #Create new column with the movie id value 
        review['MovieID'] = movie
        #Print & Create file csv
        print(review)
        review.to_csv('Review/'f'review{movie}.csv')
        driver.quit()
        
if __name__ == "__main__": get_review()

/tmp/ipykernel_55971/3476406197.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw8673424  <a href="/user/ur44965663/?ref_=tt_urv">Drawmo...   
1    rw8668903  <a href="/user/ur62070774/?ref_=tt_urv">dannyl...   
2    rw8668496  <a href="/user/ur26226712/?ref_=tt_urv">Jeremy...   
3    rw8668856  <a href="/user/ur23240045/?ref_=tt_urv">kjprou...   
4    rw8666142  <a href="/user/ur18374284/?ref_=tt_urv">MrDHWo...   
..         ...                                                ...   
698  rw8673845  <a href="/user/ur118451636/?ref_=tt_urv">iwish...   
699  rw8684679  <a href="/user/ur37607845/?ref_=tt_urv">nonimu...   
700  rw8679260  <a href="/user/ur40051567/?ref_=tt_urv">childs...   
701  rw8685895  <a href="/user/ur159053181/?ref_=tt_urv">yahya...   
702  rw8687575     <a href="/user/ur0688704/?ref_=tt_urv">drz</a>   

                User_name                                       Review_title  \
0                Drawmort                             Not what I expected...   
1          

/tmp/ipykernel_55971/3476406197.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw3574435  <a href="/user/ur52832854/?ref_=tt_urv">TouchT...   
1    rw3578519  <a href="/user/ur62164515/?ref_=tt_urv">lisaca...   
2    rw5746929  <a href="/user/ur6387867/?ref_=tt_urv">Superma...   
3    rw8557763  <a href="/user/ur78124884/?ref_=tt_urv">jaimem...   
4    rw8576876  <a href="/user/ur115536310/?ref_=tt_urv">DiCap...   
..         ...                                                ...   
782  rw5377091  <a href="/user/ur47187493/?ref_=tt_urv">jenluz...   
783  rw7206477  <a href="/user/ur55551391/?ref_=tt_urv">efrahi...   
784  rw5300610  <a href="/user/ur72665056/?ref_=tt_urv">teribi...   
785  rw4170448  <a href="/user/ur76713601/?ref_=tt_urv">faraha...   
786  rw6855765  <a href="/user/ur80805435/?ref_=tt_urv">sandyd...   

                    User_name  \
0    TouchTheGarlicProduction   
1                 lisacarlson   
2              Supermanfan-13   
3           jaimemedina-36288   
4     

/tmp/ipykernel_55971/3476406197.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


...

     Review_ID                                            User_ID  \
0    rw7393947  <a href="/user/ur0806494/?ref_=tt_urv">ferguso...   
1    rw7403291  <a href="/user/ur39322316/?ref_=tt_urv">Instan...   
2    rw7368874  <a href="/user/ur88708820/?ref_=tt_urv">shefch...   
3    rw7367097  <a href="/user/ur53958248/?ref_=tt_urv">ammarh...   
4    rw7403529  <a href="/user/ur2467618/?ref_=tt_urv">plankto...   
..         ...                                                ...   
973  rw7418460  <a href="/user/ur52346173/?ref_=tt_urv">irina-...   
974  rw7439771  <a href="/user/ur5294645/?ref_=tt_urv">hulis_</a>   
975  rw7411240  <a href="/user/ur139236678/?ref_=tt_urv">ruudw...   
976  rw7411695  <a href="/user/ur139245226/?ref_=tt_urv">mhmda...   
977  rw7494546  <a href="/user/ur96480186/?ref_=tt_urv">gustav...   

                   User_name  \
0                 ferguson-6   
1             Instant_Palmer   
2                 shefchenko   
3               ammarhammood   
4          

/tmp/ipykernel_55971/3476406197.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw1061944  <a href="/user/ur1390493/?ref_=tt_urv">Superun...   
1    rw0954031  <a href="/user/ur2637155/?ref_=tt_urv">Surecur...   
2    rw1098654  <a href="/user/ur3223254/?ref_=tt_urv">gradyha...   
3    rw3528668  <a href="/user/ur0482513/?ref_=tt_urv">Leofwin...   
4    rw0978930  <a href="/user/ur2547554/?ref_=tt_urv">ThrownM...   
..         ...                                                ...   
552  rw3087712  <a href="/user/ur34773218/?ref_=tt_urv">rbedad...   
553  rw5617823  <a href="/user/ur43154361/?ref_=tt_urv">Mohame...   
554  rw8518003  <a href="/user/ur48621861/?ref_=tt_urv">timbpi...   
555  rw1128137  <a href="/user/ur6115644/?ref_=tt_urv">turdinm...   
556  rw4504947  <a href="/user/ur96123577/?ref_=tt_urv">siddhe...   

              User_name                                       Review_title  \
0         Superunknovvn                                           A grower   
1              

/tmp/ipykernel_55971/3476406197.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


WebDriverException: Message: unknown error: net::ERR_ADDRESS_UNREACHABLE
  (Session info: chrome=106.0.5249.61)
Stacktrace:
#0 0x55b4cb6f02c3 <unknown>
#1 0x55b4cb4f983a <unknown>
#2 0x55b4cb4f3213 <unknown>
#3 0x55b4cb4e682a <unknown>
#4 0x55b4cb4e7b3d <unknown>
#5 0x55b4cb4e6b3a <unknown>
#6 0x55b4cb4e5ea5 <unknown>
#7 0x55b4cb4e5cc0 <unknown>
#8 0x55b4cb4e49bb <unknown>
#9 0x55b4cb4e4d92 <unknown>
#10 0x55b4cb4fb52e <unknown>
#11 0x55b4cb56924f <unknown>
#12 0x55b4cb550f42 <unknown>
#13 0x55b4cb568a50 <unknown>
#14 0x55b4cb550d63 <unknown>
#15 0x55b4cb5257e3 <unknown>
#16 0x55b4cb526a21 <unknown>
#17 0x55b4cb73e18e <unknown>
#18 0x55b4cb741622 <unknown>
#19 0x55b4cb724aae <unknown>
#20 0x55b4cb7422a3 <unknown>
#21 0x55b4cb718ecf <unknown>
#22 0x55b4cb762588 <unknown>
#23 0x55b4cb762706 <unknown>
#24 0x55b4cb77c8b2 <unknown>
#25 0x7f957b9efb43 <unknown>


In [2]:
def get_review():
    data = ['tt1259571', 'tt1615919', 'tt0429493', 'tt1504320', 'tt1465522', 'tt1228987', 'tt1588170', 'tt0435761', 'tt1199781', 'tt1641384', 'tt1344204', 'tt1411238', 'tt1837642', 'tt1605783', 'tt1527186', 'tt1189073', 'tt1832979', 'tt1189340', 'tt0970179', 'tt0945513', 'tt1499658', 'tt1464540', 'tt1436562', 'tt1587678', 'tt1563738', 'tt1699748', 'tt1430607', 'tt1509767', 'tt1598778', 'tt1242460', 'tt1942683', 'tt1440129', 'tt0454876', 'tt1446192', 'tt1560747', 'tt0887912', 'tt1205489', 'tt0478087', 'tt0859163', 'tt1125849', 'tt0462499', 'tt1060277', 'tt1068680', 'tt1117385', 'tt0416236', 'tt0397892', 'tt1220719', 'tt0411477', 'tt0832266', 'tt0814314', 'tt1067106', 'tt0974661', 'tt1041829', 'tt1197624', 'tt1480684', 'tt1136608', 'tt0756683', 'tt0408236', 'tt0478311', 'tt0448134', 'tt0480249', 'tt0496806', 'tt0830558', 'tt0862856', 'tt0952640', 'tt0463998', 'tt1077258', 'tt0450385', 'tt0488120', 'tt0431308', 'tt0852863', 'tt0389790', 'tt0808357', 'tt0443680', 'tt0441773', 'tt1010048', 'tt0959337', 'tt0325655', 'tt0314111', 'tt0289408', 'tt0341495', 'tt0319769', 'tt0283632', 'tt0346094', 'tt0299117', 'tt0320038', 'tt0337593', 'tt0278823', 'tt0318997', 'tt0289992', 'tt0274166', 'tt0257076', 'tt0337741', 'tt0305224', 'tt0338095', 'tt0313542', 'tt0304415', 'tt0328828', 'tt0327850', 'tt0242653', 'tt0181852', 'tt0287978', 'tt0234215', 'tt0276919', 'tt0311429', 'tt0290334', 'tt0316396', 'tt0377260', 'tt0357413', 'tt0319262', 'tt0338751', 'tt0349903', 'tt0298148', 'tt0434706', 'tt0375063', 'tt0408306', 'tt0416320', 'tt0412175', 'tt0399201', 'tt0399146', 'tt0433400', 'tt0988818', 'tt0454921', 'tt0477347', 'tt0396171', 'tt0383574', 'tt0376994', 'tt0436697', 'tt0475293', 'tt2070791', 'tt1217209', 'tt1695360', 'tt1772341', 'tt1636826', 'tt1611224', 'tt1764651', 'tt1606389', 'tt1615065', 'tt0443272', 'tt1409024', 'tt1386703', 'tt2250192', 'tt1212450', 'tt1706593', 'tt2382009', 'tt0816711', 'tt1979320', 'tt2316411', 'tt0359950', 'tt2710394', 'tt1727388', 'tt1454468', 'tt2334649', 'tt1939659', 'tt3121722', 'tt2372220', 'tt1623205', 'tt1453405', 'tt1690953', 'tt1980929', 'tt1790864', 'tt3566726', 'tt2980592', 'tt1490017', 'tt2980516', 'tt2321549', 'tt1809398', 'tt2883512', 'tt1872181', 'tt1587310', 'tt0829150', 'tt0831387', 'tt2582846', 'tt2245084', 'tt4430212', 'tt1655441', 'tt3906732', 'tt2431438', 'tt3865236', 'tt2494362', 'tt2637276', 'tt4062536', 'tt4508902', 'tt2293640', 'tt2361509', 'tt0810819', 'tt2381111', 'tt2402927', 'tt3554580', 'tt2554274', 'tt1502712', 'tt2709768', 'tt4419214', 'tt4687880', 'tt1860213', 'tt3553976', 'tt5435008', 'tt1064899', 'tt1289401', 'tt5137338', 'tt1700841', 'tt0918940', 'tt5651844', 'tt4975722', 'tt0803096', 'tt1878870', 'tt4160708', 'tt5439796', 'tt5442430', 'tt4925292', 'tt3371366', 'tt6439752', 'tt3532216', 'tt4481414', 'tt2316204', 'tt6315640', 'tt3748172', 'tt5776858', 'tt6342474', 'tt4834206', 'tt4555426', 'tt1536537', 'tt1972591', 'tt5691670', 'tt4477536', 'tt1259528', 'tt2704998', 'tt7040874', 'tt6998518', 'tt5095030', 'tt7493974', 'tt6628394', 'tt2737304', 'tt8359848', 'tt5164214', 'tt4729430', 'tt6513120', 'tt7456310', 'tt8543390', 'tt6823368', 'tt8378126', 'tt6472976', 'tt9111220', 'tt7653254', 'tt1979376', 'tt5033998', 'tt3741700', 'tt2935510', 'tt10850932', 'tt3794354', 'tt9731534', 'tt8134470', 'tt11161474', 'tt13274038', 'tt7423538', 'tt6048922', 'tt7638348', 'tt4566758', 'tt9900092', 'tt8089592', 'tt10919380', 'tt9770150', 'tt9139220', 'tt8368512', 'tt6905686', 'tt10148174', 'tt10680614', 'tt2222042', 'tt6475714', 'tt7504726', 'tt6920084', 'tt12801262', 'tt5109280', 'tt14039582', 'tt13024674', 'tt9100054', 'tt9784798', 'tt12809988', 'tt11535228', 'tt9064858', 'tt8721424', 'tt10095582', 'tt11761176', 'tt15090124', 'tt13655456', 'tt13433812', 'tt13196080', 'tt15501640', 'tt14169960', 'tt8888462']
    moviedata = pd.DataFrame(data = data, columns=['MovieID'])
    #After the webpage opened, we can extract data of each movies
    #Set initial empty list for each element:
    for i in range(len(moviedata['MovieID'])): 
        driver = webdriver.Chrome(ChromeDriverManager().install())
        url = "https://www.imdb.com/title/" + moviedata['MovieID'][i] + "/reviews?"
        driver.get(url)
        # tell the webdriver to wait for 3 seconds for the page to load to prevent blocked by anti spam software
        driver.implicitly_wait(3) 
        # Set up action to click on 'load more' button
        # note that each page on imdb has 25 reviews
        page = 1 #Set initial variable for while loop
        #Get 0-1000 review => get at least 40 page
        while page<40:  
            try:
                #find the load more button on the webpage
                load_more = driver.find_element(By.ID, 'load-more-trigger')
                #click on that button
                load_more.click()
                page+=1 #move on to next loadmore button
            except:
                #If couldnt find any button to click, stop
                break
        # After fully expand the page, we will grab data from whole website
        review = driver.find_elements(By.CLASS_NAME, 'lister-item')
        #Set list for each element:
        title = []
        review_id = []
        content = []
        rate = []
        date = []
        user_id = []
        user_name = []
        #run for loop to get 
        for n in range(0,10000):
            try:
                #Grab each element before append them to the list
                reviewtitle = review[n].find_element(By.CLASS_NAME, 'title').text
                reviewcontent = review[n].find_element(By.CLASS_NAME, 'content').get_attribute("textContent")
                reviewrate = review[n].find_element(By.CLASS_NAME, 'rating-other-user-rating').text
                reviewdate = review[n].find_element(By.CLASS_NAME, 'review-date').text
                userid = review[n].find_element(By.CLASS_NAME, 'display-name-link').get_attribute("innerHTML")
                username = review[n].find_element(By.CLASS_NAME, 'display-name-link').text
                reviewid = review[n].get_attribute('data-review-id')

                #Then add them to the respective list
                review_id.append(reviewid)
                user_id.append(userid)
                title.append(reviewtitle)
                content.append(reviewcontent)
                rate.append(reviewrate)
                date.append(reviewdate)
                user_name.append(username)
            except:
                continue
        #Build data dictionary for dataframe
        reviewdata = {'Review_ID' : review_id,
                    'User_ID' : user_id,
                    'User_name' : user_name,
                    'Review_title' : title, 
                    'Review_rate' : rate,
                    'Review_date' : date,
                    'Review_body' : content}
        #Build dataframe for each review movie to export
        review = pd.DataFrame(data = reviewdata)
        movie = moviedata['MovieID'][i] 
        #create new column with the movie id value 
        review['MovieID'] = movie
        #Print & Create file csv
        print(review)    
        review.to_csv('Review/'f'review{movie}.csv')
        driver.quit()
        
if __name__ == "__main__": get_review()

/tmp/ipykernel_741635/350632382.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw2418441  <a href="/user/ur19511193/?ref_=tt_urv">Samiam...   
1    rw2611742  <a href="/user/ur13977076/?ref_=tt_urv">Tweeku...   
2    rw2336314  <a href="/user/ur0375636/?ref_=tt_urv">Buddy-5...   
3    rw2262927  <a href="/user/ur17510062/?ref_=tt_urv">sjmutc...   
4    rw2383818  <a href="/user/ur4248714/?ref_=tt_urv">jboothm...   
..         ...                                                ...   
758  rw2298500  <a href="/user/ur23747087/?ref_=tt_urv">mwinga...   
759  rw6025159  <a href="/user/ur56408491/?ref_=tt_urv">sophan...   
760  rw2169859  <a href="/user/ur6867740/?ref_=tt_urv">Karl_Cr...   
761  rw8570729  <a href="/user/ur74489266/?ref_=tt_urv">mikewo...   
762  rw2163962  <a href="/user/ur9916709/?ref_=tt_urv">derum-1...   

          User_name                                   Review_title  \
0           Samiam3   Beautiful people, big box office, zero story   
1          Tweekums            

/tmp/ipykernel_741635/350632382.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


    Review_ID                                            User_ID  \
0   rw7075644  <a href="/user/ur76888172/?ref_=tt_urv">jsucie...   
1   rw2314060  <a href="/user/ur0105327/?ref_=tt_urv">Bronco4...   
2   rw2329382  <a href="/user/ur23748553/?ref_=tt_urv">renewe...   
3   rw2316555  <a href="/user/ur9931772/?ref_=tt_urv">cadetgr...   
4   rw5658319  <a href="/user/ur71966883/?ref_=tt_urv">micah-...   
..        ...                                                ...   
79  rw7867886  <a href="/user/ur149954974/?ref_=tt_urv">nanch...   
80  rw3507691  <a href="/user/ur67977321/?ref_=tt_urv">fatkid...   
81  rw8477341  <a href="/user/ur156036725/?ref_=tt_urv">mamad...   
82  rw2326656  <a href="/user/ur5375817/?ref_=tt_urv">chronol...   
83  rw4040598  <a href="/user/ur84660079/?ref_=tt_urv">mrchar...   

           User_name                                       Review_title  \
0             jsucie                    Underrated Brilliance Cut Short   
1           Bronco46             

/tmp/ipykernel_741635/350632382.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


...

    Review_ID                                            User_ID  \
0   rw8681685  <a href="/user/ur22864666/?ref_=tt_urv">ketgup...   
1   rw8680525  <a href="/user/ur117097528/?ref_=tt_urv">samee...   
2   rw8685601  <a href="/user/ur134646264/?ref_=tt_urv">manit...   
3   rw8685779  <a href="/user/ur27103055/?ref_=tt_urv">saurav...   
4   rw8684433  <a href="/user/ur51103248/?ref_=tt_urv">keeran...   
..        ...                                                ...   
75  rw8691059  <a href="/user/ur159147802/?ref_=tt_urv">divye...   
76  rw8692550  <a href="/user/ur20151610/?ref_=tt_urv">john-c...   
77  rw8692571  <a href="/user/ur37330400/?ref_=tt_urv">nynvai...   
78  rw8687612  <a href="/user/ur48699080/?ref_=tt_urv">shabbi...   
79  rw8685082  <a href="/user/ur61770054/?ref_=tt_urv">naveen...   

             User_name                             Review_title Review_rate  \
0             ketgup83                          Faithful remake        8/10   
1         sameerlodaya   

/tmp/ipykernel_741635/350632382.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw7807211  <a href="/user/ur18426527/?ref_=tt_urv">diesco...   
1    rw7902930  <a href="/user/ur0482513/?ref_=tt_urv">Leofwin...   
2    rw7822362  <a href="/user/ur79190944/?ref_=tt_urv">andrew...   
3    rw7816875  <a href="/user/ur1315860/?ref_=tt_urv">captain...   
4    rw7807314  <a href="/user/ur20622295/?ref_=tt_urv">Snowno...   
..         ...                                                ...   
267  rw7854535  <a href="/user/ur72270574/?ref_=tt_urv">spring...   
268  rw8010794  <a href="/user/ur45428362/?ref_=tt_urv">Speeke...   
269  rw8076037  <a href="/user/ur46572565/?ref_=tt_urv">umeshw...   
270  rw7824561  <a href="/user/ur74575423/?ref_=tt_urv">FritzS...   
271  rw7809492  <a href="/user/ur149118759/?ref_=tt_urv">alpha...   

             User_name                                       Review_title  \
0         diescobarmdq                                        Holy s***t!   
1       Leofwine_

/tmp/ipykernel_741635/350632382.py:8: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


     Review_ID                                            User_ID  \
0    rw8003006  <a href="/user/ur89157373/?ref_=tt_urv">tradem...   
1    rw8009408  <a href="/user/ur33079525/?ref_=tt_urv">yooniv...   
2    rw8011704  <a href="/user/ur0179443/?ref_=tt_urv">DukeEma...   
3    rw8019398  <a href="/user/ur109409320/?ref_=tt_urv">nkili...   
4    rw8003929  <a href="/user/ur101529160/?ref_=tt_urv">Pardo...   
..         ...                                                ...   
123  rw8103592  <a href="/user/ur94704679/?ref_=tt_urv">victor...   
124  rw8043822  <a href="/user/ur151802415/?ref_=tt_urv">starr...   
125  rw8292675  <a href="/user/ur154231029/?ref_=tt_urv">terrp...   
126  rw8292957  <a href="/user/ur154234965/?ref_=tt_urv">tonya...   
127  rw8327706  <a href="/user/ur45552955/?ref_=tt_urv">eric-7...   

                  User_name  \
0          trademarcdesigns   
1                yooniverse   
2                  DukeEman   
3                  nkiliuzo   
4            Par

In [ ]:
def get_review():
    
    data = ['tt13406094', 'tt6226232', 'tt2935622']
    # Create the pandas DataFrame
    moviedata = pd.DataFrame(data, columns=['movieid'])
    #After the webpage opened, we can extract data of each movies
    #Set initial empty list for each element:
    for i in range(len(moviedata['movieid'])): 
        driver = webdriver.Chrome(ChromeDriverManager().install())
        url = "https://www.imdb.com/title/" + moviedata['movieid'][i] + "/reviews?"
        driver.get(url)
        driver.implicitly_wait(3) # tell the webdriver to wait for 3 seconds for the page to load to prevent blocked by anti spam software
        # Set up action to click on 'load more' button
        # note that each page on imdb has 25 reviews
        page = 1 #Set initial variable for while loop
        #Test at least 5 pages
        while page<5:  
            try:
                #find the load more button on the webpage
                load_more = driver.find_element(By.ID, 'load-more-trigger')
                #click on that button
                load_more.click()
                page+=1 #move on to next loadmore button
            except:
                #If couldnt find any button to click, stop
                break
        # After fully expand the page, we will grab data from whole website
        review = driver.find_elements(By.CLASS_NAME, 'lister-item')
        #Set list for each element:
        title = []
        review_id = []
        content = []
        rate = []
        date = []
        user_id = []
        user_name = []
        #run for loop to get 
        for n in range(0,50):
            try:
                #Grab each element before append them to the list
                reviewtitle = review[n].find_element(By.CLASS_NAME, 'title').text
                reviewcontent = review[n].find_element(By.CLASS_NAME, 'content').get_attribute("textContent")
                reviewrate = review[n].find_element(By.CLASS_NAME, 'rating-other-user-rating').text
                reviewdate = review[n].find_element(By.CLASS_NAME, 'review-date').text
                userid = review[n].find_element(By.CLASS_NAME, 'display-name-link').get_attribute("innerHTML")
                username = review[n].find_element(By.CLASS_NAME, 'display-name-link').text
                reviewid = review[n].get_attribute('data-review-id')

                #Then add them to list
                review_id.append(reviewid)
                user_id.append(userid)
                title.append(reviewtitle)
                content.append(reviewcontent)
                rate.append(reviewrate)
                date.append(reviewdate)
                user_name.append(username)
            except:
                continue
        #Build data dictionary for dataframe
        reviewdata = {'Review_ID' : review_id,
                    'User_ID' : user_id,
                    'User_name' : user_name,
                    'Review_title' : title, 
                    'Review_rate' : rate,
                    'Review_date' : date,
                    'Review_body' : content}
        #Build dataframe for each review movie to export
        review = pd.DataFrame(data = reviewdata)
        movie = moviedata['movieid'][i] 
        #create new column with the movie id value 
        review['movieid'] = movie
        #Print & Create file csv
        print(review)    
        review.to_csv('Review/Test/'f'review{movie}.csv')
        driver.quit()
        
if __name__ == "__main__": get_review()